inspired by https://github.com/Data-Monkey/GTFS-NetworkX/blob/master/GTFStoGraph.py

GTFS API: https://developers.google.com/transit/gtfs/reference#agencytxt

In [45]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import networkx as nx

### Import the GTFS Files

In [105]:
ROUTES = pd.read_csv('cta_data/routes.txt')
STOPS = pd.read_csv('cta_data/stops.txt')
TRIPS = pd.read_csv('cta_data/trips.txt')
STOP_TIMES = pd.read_csv('cta_data/stop_times.txt')

### Clean the Data for "L" Train info only

We (for now) only want to model subways/metros, which use `route_type=1`, so we get a list of the `route_id`s that correspond ot the subway ("L") lines

In [109]:
ROUTES_subway = ROUTES[ROUTES['route_type']==1]
route_ids_subway = ROUTES_subway['route_id'].values.tolist()
ROUTES_subway

route_id route_short_name route_long_name  route_type  \
126      Red              NaN        Red Line           1   
127        P              NaN     Purple Line           1   
128        Y              NaN     Yellow Line           1   
129     Blue              NaN       Blue Line           1   
130     Pink              NaN       Pink Line           1   
131        G              NaN      Green Line           1   
132      Org              NaN     Orange Line           1   
133      Brn              NaN      Brown Line           1   

                                     route_url route_color route_text_color  
126     http://www.transitchicago.com/redline/      C60C30           FFFFFF  
127  http://www.transitchicago.com/purpleline/      522398           FFFFFF  
128  http://www.transitchicago.com/yellowline/      F9E300           000000  
129    http://www.transitchicago.com/blueline/      00A1DE           FFFFFF  
130    http://www.transitchicago.com/pinkline/      E27EA6           FFFFFF  
131   http://www.transitchicago.com/greenline/      009B3A           FFFFFF  
132  http://www.transitchicago.com/orangeline/      F9461C           FFFFFF  
133   http://www.transitchicago.com/brownline/      62361B           FFFFFF

Likewise, we will filter the `TRIPS` data so that it only includes trips for subway routes:

In [133]:
TRIPS_subway = TRIPS[TRIPS['route_id'].isin(route_ids_subway)]
# only include one direction to avoid redundancies
TRIPS_subway = TRIPS_subway[TRIPS_subway['direction_id']==0]
trip_ids_subway = list(TRIPS_subway['trip_id'].values)
TRIPS_subway

route_id  service_id      trip_id  direction_id     block_id   shape_id  \
41968     Blue      106001  60166141079             0  60015964047  306000002   
41969     Blue      106001  60166141080             0  60015964047  306000002   
41971     Blue      106001  60166141085             0  60015963974  306000002   
41973     Blue      106001  60166141087             0  60015963974  306000002   
41975     Blue      106001  60166141089             0  60015963973  306000074   
...        ...         ...          ...           ...          ...        ...   
47041        Y      106009  60161865594             0  60015582422  306000033   
47042        Y      106009  60161865595             0  60015582423  306000033   
47043        Y      106009  60161865597             0  60015582422  306000033   
47044        Y      106009  60161865598             0  60015582423  306000033   
47045        Y      106009  60161865599             0  60015582423  306000033   

      direction  wheelchair_accessible schd_trip_id  
41968     South                      1         R133  
41969     South                      1         R219  
41971     South                      1         R146  
41973     South                      1         R107  
41975     South                      1         R203  
...         ...                    ...          ...  
47041         0                      1         R593  
47042         0                      1         R594  
47043         0                      1         R591  
47044         0                      1         R592  
47045         0                      1         R594  

[2280 rows x 9 columns]

In [135]:
STOP_TIMES_subway = STOP_TIMES[STOP_TIMES['trip_id'].isin(trip_ids_subway)]
STOP_TIMES_subway

trip_id arrival_time departure_time  stop_id  stop_sequence  \
0       60161865358     06:31:00       06:31:00    30175              1   
1       60161865358     06:37:30       06:37:30    30297              2   
2       60161865358     06:39:00       06:39:00    30026              3   
3       60161865358     06:45:00       06:45:00    30027              4   
4       60161865358     06:47:00       06:47:00    30298              5   
...             ...          ...            ...      ...            ...   
144277  60166204801     21:54:30       21:54:30    30282              8   
144278  60166204801     21:55:30       21:55:30    30278              9   
144279  60166204801     21:57:30       21:57:30    30254             10   
144280  60166204801     21:58:30       21:58:30    30071             11   
144281  60166204801     22:01:00       22:01:00    30258             12   

       stop_headsign  pickup_type  shape_dist_traveled  
0             Skokie            0                    0  
1             Skokie            0                21220  
2             Skokie            0                26031  
3             Howard            0                26031  
4             Howard            0                30842  
...              ...          ...                  ...  
144277          Loop            0                15016  
144278          Loop            0                17748  
144279          Loop            0                19774  
144280          Loop            0                21752  
144281          Loop            0                25799  

[67844 rows x 8 columns]

We only want to track `stations` (`location_type=1`), but `STOP_TIMES` gives information for `platforms`(`location_type=0`). So first we need to assign the parent for each of the stops in `STOP_TIMES`

In [136]:
STOPS_stations = STOPS[STOPS['location_type']==1]
stop_ids_stations = list(STOPS_stations['stop_id'].unique())

In [137]:
def get_parent(stop_id):
    parent = STOPS[STOPS['stop_id']==stop_id]['parent_station'].values
    if len(parent) == 0:
        return stop_id
    else:
        return parent[0]

STOP_TIMES_subway['station_id'] = STOP_TIMES_subway['stop_id'].apply(get_parent)

<ipython-input-137-17e115b19e62>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  STOP_TIMES_subway['station_id'] = STOP_TIMES_subway['stop_id'].apply(get_parent)


### use trip information to determine graph edges

In [97]:
# origin_stops = []
# dest_stops = []
# trip_ids = []

edges_list = []
for trip_id, group in STOP_TIMES_subway.groupby('trip_id'):
    for i in group.index[:-1]:
        origin_stop = STOP_TIMES_subway['station_id'][i]
        dest_stop = STOP_TIMES_subway['station_id'][i+1]

#         origin_stops.append(origin_stop)
#         dest_stops.append(dest_stop)
#         trip_ids.append(trip_id)
        edges_list.append((origin_stop, dest_stop))

60161865358 40900.0 41680.0
60161865358 41680.0 40140.0
60161865358 40140.0 40140.0
60161865358 40140.0 41680.0
60161865358 41680.0 40900.0
60161865359 40900.0 41680.0
60161865359 41680.0 40140.0
60161865359 40140.0 40140.0
60161865359 40140.0 41680.0
60161865359 41680.0 40900.0
60161865360 40900.0 41680.0
60161865360 41680.0 40140.0
60161865360 40140.0 40140.0
60161865360 40140.0 41680.0
60161865360 41680.0 40900.0
60161865361 40900.0 41680.0
60161865361 41680.0 40140.0
60161865361 40140.0 40140.0
60161865361 40140.0 41680.0
60161865361 41680.0 40900.0
60161865362 40900.0 41680.0
60161865362 41680.0 40140.0
60161865362 40140.0 40140.0
60161865362 40140.0 41680.0
60161865362 41680.0 40900.0
60161865363 40900.0 41680.0
60161865363 41680.0 40140.0
60161865363 40140.0 40140.0
60161865363 40140.0 41680.0
60161865363 41680.0 40900.0
60161865364 40900.0 41680.0
60161865364 41680.0 40140.0
60161865364 40140.0 40140.0
60161865364 40140.0 41680.0
60161865364 41680.0 40900.0
60161865365 40900.0 

60161865430 40400.0 41250.0
60161865430 41250.0 41050.0
60161865430 41050.0 41050.0
60161865430 41050.0 41250.0
60161865430 41250.0 40400.0
60161865430 40400.0 40520.0
60161865430 40520.0 40050.0
60161865430 40050.0 40690.0
60161865430 40690.0 40270.0
60161865430 40270.0 40840.0
60161865430 40840.0 40900.0
60161865431 40900.0 40840.0
60161865431 40840.0 40270.0
60161865431 40270.0 40690.0
60161865431 40690.0 40050.0
60161865431 40050.0 40520.0
60161865431 40520.0 40400.0
60161865431 40400.0 41250.0
60161865431 41250.0 41050.0
60161865431 41050.0 41050.0
60161865431 41050.0 41250.0
60161865431 41250.0 40400.0
60161865431 40400.0 40520.0
60161865431 40520.0 40050.0
60161865431 40050.0 40690.0
60161865431 40690.0 40270.0
60161865431 40270.0 40840.0
60161865431 40840.0 40900.0
60161865432 40900.0 40840.0
60161865432 40840.0 40270.0
60161865432 40270.0 40690.0
60161865432 40690.0 40050.0
60161865432 40050.0 40520.0
60161865432 40520.0 40400.0
60161865432 40400.0 41250.0
60161865432 41250.0 

60161865457 40900.0 40840.0
60161865457 40840.0 40270.0
60161865457 40270.0 40690.0
60161865457 40690.0 40050.0
60161865457 40050.0 40520.0
60161865457 40520.0 40400.0
60161865457 40400.0 41250.0
60161865457 41250.0 41050.0
60161865457 41050.0 41050.0
60161865457 41050.0 41250.0
60161865457 41250.0 40400.0
60161865457 40400.0 40520.0
60161865457 40520.0 40050.0
60161865457 40050.0 40690.0
60161865457 40690.0 40270.0
60161865457 40270.0 40840.0
60161865457 40840.0 40900.0
60161865458 40900.0 40840.0
60161865458 40840.0 40270.0
60161865458 40270.0 40690.0
60161865458 40690.0 40050.0
60161865458 40050.0 40520.0
60161865458 40520.0 40400.0
60161865458 40400.0 41250.0
60161865458 41250.0 41050.0
60161865458 41050.0 41050.0
60161865458 41050.0 41250.0
60161865458 41250.0 40400.0
60161865458 40400.0 40520.0
60161865458 40520.0 40050.0
60161865458 40050.0 40690.0
60161865458 40690.0 40270.0
60161865458 40270.0 40840.0
60161865458 40840.0 40900.0
60161865459 40900.0 40840.0
60161865459 40840.0 

60161865484 40520.0 40050.0
60161865484 40050.0 40690.0
60161865484 40690.0 40270.0
60161865484 40270.0 40840.0
60161865484 40840.0 40900.0
60161865485 40900.0 40840.0
60161865485 40840.0 40270.0
60161865485 40270.0 40690.0
60161865485 40690.0 40050.0
60161865485 40050.0 40520.0
60161865485 40520.0 40400.0
60161865485 40400.0 41250.0
60161865485 41250.0 41050.0
60161865485 41050.0 41050.0
60161865485 41050.0 41250.0
60161865485 41250.0 40400.0
60161865485 40400.0 40520.0
60161865485 40520.0 40050.0
60161865485 40050.0 40690.0
60161865485 40690.0 40270.0
60161865485 40270.0 40840.0
60161865485 40840.0 40900.0
60161865486 40900.0 40840.0
60161865486 40840.0 40270.0
60161865486 40270.0 40690.0
60161865486 40690.0 40050.0
60161865486 40050.0 40520.0
60161865486 40520.0 40400.0
60161865486 40400.0 41250.0
60161865486 41250.0 41050.0
60161865486 41050.0 41050.0
60161865486 41050.0 41250.0
60161865486 41250.0 40400.0
60161865486 40400.0 40520.0
60161865486 40520.0 40050.0
60161865486 40050.0 

60161865513 40900.0 40840.0
60161865513 40840.0 40270.0
60161865513 40270.0 40690.0
60161865513 40690.0 40050.0
60161865513 40050.0 40520.0
60161865513 40520.0 40400.0
60161865513 40400.0 41250.0
60161865513 41250.0 41050.0
60161865513 41050.0 41050.0
60161865513 41050.0 41250.0
60161865513 41250.0 40400.0
60161865513 40400.0 40520.0
60161865513 40520.0 40050.0
60161865513 40050.0 40690.0
60161865513 40690.0 40140.0
60161865513 40270.0 40840.0
60161865513 40840.0 40900.0
60161865514 40900.0 40840.0
60161865514 40840.0 40270.0
60161865514 40270.0 40690.0
60161865514 40690.0 40050.0
60161865514 40050.0 40520.0
60161865514 40520.0 40400.0
60161865514 40400.0 41250.0
60161865514 41250.0 41050.0
60161865514 41050.0 41050.0
60161865514 41050.0 41250.0
60161865514 41250.0 40400.0
60161865514 40400.0 40520.0
60161865514 40520.0 40050.0
60161865514 40050.0 40690.0
60161865514 40690.0 40270.0
60161865514 40270.0 40840.0
60161865514 40840.0 40900.0
60161865515 40900.0 40840.0
60161865515 40840.0 

...

60166204803 41310.0 40360.0
60166204803 40360.0 41320.0
60166204803 41320.0 41210.0
60166204803 41210.0 40530.0
60166204803 40530.0 41220.0
60166204803 41220.0 40660.0
60166204803 40660.0 40800.0
60166204803 40800.0 40710.0
60166204803 40710.0 40460.0
60166204803 40460.0 40730.0
60166204803 40730.0 40040.0
60166204803 40040.0 40160.0
60166204803 40160.0 40850.0
60166204803 40850.0 40680.0
60166204803 40680.0 41700.0
60166204803 41700.0 40260.0
60166204803 40260.0 40380.0
60166204803 40380.0 40460.0
60166204803 40460.0 40710.0
60166204803 40710.0 40800.0
60166204803 40800.0 40660.0
60166204803 40660.0 41220.0
60166204803 41220.0 40530.0
60166204803 40530.0 41210.0
60166204803 41210.0 41320.0
60166204803 41320.0 40360.0
60166204803 40360.0 41310.0
60166204803 41310.0 41440.0
60166204803 41440.0 41460.0
60166204803 41460.0 41500.0
60166204803 41500.0 40090.0
60166204803 40090.0 41480.0
60166204803 41480.0 41010.0
60166204803 41010.0 40870.0
60166204803 40870.0 41180.0
60166204803 41180.0 

60166204924 40930.0 40960.0
60166204924 40960.0 41150.0
60166204924 41150.0 40310.0
60166204924 40310.0 40120.0
60166204924 40120.0 41060.0
60166204924 41060.0 41130.0
60166204924 41130.0 41400.0
60166204924 41400.0 40850.0
60166204924 40850.0 40160.0
60166204924 40160.0 40040.0
60166204924 40040.0 40730.0
60166204924 40730.0 40380.0
60166204924 40380.0 40260.0
60166204924 40260.0 41700.0
60166204924 41700.0 40680.0
60166204924 40680.0 41400.0
60166204924 41400.0 41130.0
60166204924 41130.0 41060.0
60166204924 41060.0 40120.0
60166204924 40120.0 40310.0
60166204924 40310.0 41150.0
60166204924 41150.0 40960.0
60166204924 40960.0 40930.0
60166204925 40930.0 40960.0
60166204925 40960.0 41150.0
60166204925 41150.0 40310.0
60166204925 40310.0 40120.0
60166204925 40120.0 41060.0
60166204925 41060.0 41130.0
60166204925 41130.0 41400.0
60166204925 41400.0 40850.0
60166204925 40850.0 40160.0
60166204925 40160.0 40040.0
60166204925 40040.0 40730.0
60166204925 40730.0 40380.0
60166204925 40380.0 

60166204950 41150.0 40310.0
60166204950 40310.0 40120.0
60166204950 40120.0 41060.0
60166204950 41060.0 41130.0
60166204950 41130.0 41400.0
60166204950 41400.0 40850.0
60166204950 40850.0 40160.0
60166204950 40160.0 40040.0
60166204950 40040.0 40730.0
60166204950 40730.0 40380.0
60166204950 40380.0 40260.0
60166204950 40260.0 41700.0
60166204950 41700.0 40680.0
60166204950 40680.0 41400.0
60166204950 41400.0 41130.0
60166204950 41130.0 41060.0
60166204950 41060.0 40120.0
60166204950 40120.0 40310.0
60166204950 40310.0 41150.0
60166204950 41150.0 40960.0
60166204950 40960.0 40930.0
60166204951 40930.0 40960.0
60166204951 40960.0 41150.0
60166204951 41150.0 40310.0
60166204951 40310.0 40120.0
60166204951 40120.0 41060.0
60166204951 41060.0 41130.0
60166204951 41130.0 41400.0
60166204951 41400.0 40850.0
60166204951 40850.0 40160.0
60166204951 40160.0 40040.0
60166204951 40040.0 40730.0
60166204951 40730.0 40380.0
60166204951 40380.0 40260.0
60166204951 40260.0 41700.0
60166204951 41700.0 

60166204972 40930.0 40960.0
60166204972 40960.0 41150.0
60166204972 41150.0 40310.0
60166204972 40310.0 40120.0
60166204972 40120.0 41060.0
60166204972 41060.0 41130.0
60166204972 41130.0 41400.0
60166204972 41400.0 40850.0
60166204972 40850.0 40160.0
60166204972 40160.0 40040.0
60166204972 40040.0 40730.0
60166204972 40730.0 40380.0
60166204972 40380.0 40260.0
60166204972 40260.0 41700.0
60166204972 41700.0 40680.0
60166204972 40680.0 41400.0
60166204972 41400.0 41130.0
60166204972 41130.0 41060.0
60166204972 41060.0 40120.0
60166204972 40120.0 40310.0
60166204972 40310.0 41150.0
60166204972 41150.0 40960.0
60166204972 40960.0 40930.0
60166204973 40930.0 40960.0
60166204973 40960.0 41150.0
60166204973 41150.0 40310.0
60166204973 40310.0 40120.0
60166204973 40120.0 41060.0
60166204973 41060.0 41130.0
60166204973 41130.0 41400.0
60166204973 41400.0 40850.0
60166204973 40850.0 40160.0
60166204973 40160.0 40040.0
60166204973 40040.0 40730.0
60166204973 40730.0 40380.0
60166204973 40380.0 

KeyError: 141637

In [130]:
len(STOP_TIMES_subway['trip_id'].unique())

4420

In [61]:
edges = pd.DataFrame({'origin_stop':origin_stops, 'dest_stop':dest_stops, 'trip_id':trip_ids})

In [62]:
edges

origin_stop  dest_stop      trip_id
0             30175      30297  60161865358
1             30297      30026  60161865358
2             30026      30027  60161865358
3             30027      30298  60161865358
4             30298      30176  60161865358
...             ...        ...          ...
128381        30206      30023  60166205118
128382        30023      30061  60166205118
128383        30061      30220  60166205118
128384        30220      30186  60166205118
128385        30186      30182  60166205118

[128386 rows x 3 columns]

In [ ]:
G = nx.Graph()

G.add_nodes_from(edge_list)